In [2]:
import pandas as pd
import numpy as np
import random
from functools import reduce

In [4]:
df = pd.read_csv("info.csv").iloc[:,1:]
df = df.set_index("Your name")

In [5]:
df

First Person   Second person  Third person  Fourth person  \
Your name                                                              
1                   13.0           12.0          78.0            8.0   
2                   61.0           42.0          39.0            3.0   
3                   61.0           39.0           2.0           69.0   
4                   37.0           21.0          14.0           28.0   
5                   43.0            7.0          30.0           41.0   
...                  ...            ...           ...            ...   
90                   NaN            NaN           NaN            NaN   
91                   NaN            NaN           NaN            NaN   
92                   NaN            NaN           NaN            NaN   
93                   NaN            NaN           NaN            NaN   
94                   NaN            NaN           NaN            NaN   

           Fifth person  
Your name                
1                  34.0  
2                  69.0  
3                  44.0  
4                  51.0  
5                  32.0  
...                 ...  
90                  NaN  
91                  NaN  
92                  NaN  
93                  NaN  
94                  NaN  

[94 rows x 5 columns]

In [6]:
class Evaluation:  
    def VerticleHappiness(self, people):
        HappyPeople = []
        for person in people:
            row, col = self.getRowColFromPerson(person)

            choices = self.getChoices(person)

            if row!=self.numRows-1:
                p = self.Chart[row+1][col]
                rank = self.rank(p,choices)

                if rank in range(1,6) and person not in HappyPeople:
                    HappyPeople.append(person)


            if row!=0:
                p = self.Chart[row-1][col]

                rank = self.rank(p,choices)
 
                if rank in range(1,6) and person not in HappyPeople:
                    HappyPeople.append(person)
        print("Number of People with verticle: %s "%HappyPeople)
            
    def rank(self,p,choices):
        if p in choices: return choices.index(p)+1
        return None
    
    def EvaluateHappiness(self):
        
        Done = []
        for Level in range(1,6):
            
            HappyPeople = []
            NoPreferences = []
            UnHappyPeople = []
            
            for row in range(self.numRows):
                for col in range(self.numCols):
                    person = self.Chart[row][col]
                    if person==0: continue
                
                    if self.NaPerson(person): 
                        NoPreferences.append(person)
                        continue

                    choices = self.getChoices(person)
                    
                    if col!=self.numCols-1:
                        p = self.Chart[row][col+1]
                        
                        rank = self.rank(p,choices)
                        if rank == Level and person not in HappyPeople and person not in Done: 
                            HappyPeople.append(person)
                        
                        
                    if col!=0:
                        p = self.Chart[row][col-1]
                        rank = self.rank(p,choices)
                        
                        if rank == Level and person not in HappyPeople and person not in Done:
                            HappyPeople.append(person)
                        
                        
           
            print("Level %s, # of people %s" %(Level, len(HappyPeople)))
            Done += HappyPeople
                            
        print("# of people No Preferences", len(NoPreferences))
        
        print("Not in Top 5:", 94-len(NoPreferences)-len(Done))
        UnHappyPeople = [p for p in range(1,95) if p not in NoPreferences+Done]
        print("Not in Top 5:", UnHappyPeople)
        self.VerticleHappiness(UnHappyPeople)
        
        

In [7]:
class FunctionTools:
    def getRowColFromPerson(self,person):
        for row in range(self.numRows):
                for col in range(self.numCols):
                    p = self.Chart[row][col]
                    
                    if person==p:
                        
                        return row,col
                    
    def idealPairs(self):
        self.firsts = []
        for pair in self.matches:
            if pair["rank1"] in [1,2,None] and pair["rank2"] in [1,2,None]:
                self.firsts.append(pair)
    
    def makeDict(self, person1, rank1, person2, rank2):
        return {"person1":person1,"rank1":rank1,"person2":person2, "rank2":rank2}
    
    def getChoices(self,p):
        return list(self.df.loc[p])
    
    def removePersonFromMatches(self,person):
        return [pair for pair in matches if not (pair["person1"]==person or pair["person2"]==person)]
    
    def removePersonFromPeople(self,p, people):
        return [person for person in people if person != p]
        
                
    def getMatches(self,person):
        return [pair for pair in self.matches if pair["person1"]==person or pair["person2"]==person]
    
    
    def NaPerson(self,person):
        choices = self.getChoices(person)
        return np.isnan(choices).all()         
    
    def getPeople(self,pair):
        return [pair["person1"],pair["person2"]]
    
    def CompositeScore(self, pair):
        rank1 = pair["rank1"]
        rank2 = pair["rank2"]
        totalRank = rank2*2 if rank1 == None else (rank1*2 if rank2==None else rank1+rank2)
        return totalRank
    
    def findOtherPerson(self,pair, person):
        return pair["person1"] if person != pair["person1"] else pair["person2"]
    
    def findMatchPeople(self,matchesLeft,personLeft, matchesAbove, personAbove):
        peopleLeft = [self.findOtherPerson(pair, personLeft) for pair in matchesLeft]
        peopleAbove = [self.findOtherPerson(pair, personAbove) for pair in matchesAbove]
        return list(set(peopleLeft).union(set(peopleAbove)))
    
    def samePeople(self,pair, p1,p2):
        np1, np2 = pair["person1"],pair["person2"]
        if (np1 == p1 and np2==p2) or (np2 == p1 and np1==p2):
            return True
        return False
    
    
    def getMatch(self,p1,p2):
        match = [pair for pair in self.matches if self.samePeople(pair,p1,p2)]
        if len(match)==0:return None
        return match[0]
    
    def scorePair(self, pair):
        rank1 = pair["rank1"]
        rank2 = pair["rank2"]
        totalRank = rank2*2 if rank1 == None else (rank1*2 if rank2==None else rank1+rank2)
        return totalRank
    

In [33]:

class Students(Evaluation, FunctionTools):
    df = pd.read_csv("info.csv").iloc[:,1:]
    df = df.set_index("Your name")
    def __init__(self):
        self.numCols = 10
        self.numRows = 10
        self.matches()
        self.idealPairs()
        self.MatchesForLonelyPeople()
        self.stringPairs = []
        self.people = list(self.df.index)
        
        self.Chart = np.zeros((self.numRows,self.numCols))
        
      
        #self.Chart[0][0] = 40
        #print(self.lowestCompositeScore(0,1))
        self.createString(0,0, self.people)
        #self.EvaluateHappiness()

        
    def matches(self):
        matches = []
        for person,rankings in self.df.iterrows():
                for rank1,rankedPerson in enumerate(rankings):
                    if not pd.isnull(rankedPerson):
                        OtherPersonChoices = self.getChoices(rankedPerson)
                        if person in OtherPersonChoices:
                            if person > rankedPerson: continue #don't want duplicates if they overlap it will be added by first person
                            rank2 = OtherPersonChoices.index(person)
                            matches.append(self.makeDict(person,rank1+1,rankedPerson,rank2))
                        elif np.isnan(OtherPersonChoices).all():
                            matches.append(self.makeDict(person,rank1+1,rankedPerson,None))
        self.matches = matches
    
    def NoMatches(self):
        haveMatch = reduce(lambda a,b: a+b, [self.getPeople(pair) for pair in self.matches])
        return [p for p in range(1,95) if p not in haveMatch and not self.NaPerson(p)]
    
    def MatchesForLonelyPeople(self):
        needMatch = self.NoMatches()
        for person in needMatch:
            rankings = self.getChoices(person)
            for rank1,rankedPerson in enumerate(rankings):
                if not pd.isnull(rankedPerson):
                    self.matches.append(self.makeDict(person,rank1+1,rankedPerson,rank1+1))
                    
    def CompositeScore(self,person,personLeft, personAbove):
        if len(self.getMatches(person))==1: return -100
        matchLeft = self.getMatch(person,personLeft)
        matchAbove = self.getMatch(person,personAbove)
        
        if matchAbove == None:
            totalRankLeft = self.scorePair(matchLeft)
            return totalRankLeft
        if matchLeft == None:
            totalRankAbove = self.scorePair(matchAbove)
            return 100+totalRankAbove
        
        totalRankLeft = self.scorePair(matchLeft)
        totalRankAbove = 12-self.scorePair(matchAbove)
        return totalRankLeft-.5*(totalRankAbove)
        
    def lowestCompositeScore(self, row,col, people):
        
        personLeft = 0 if col==0 else self.Chart[row][col-1]
        personAbove = 0 if row==0 else self.Chart[row-1][col]
        if (personLeft==0 and personAbove==0): return None
        matchesLeft = self.getMatches(personLeft)
        matchesAbove = self.getMatches(personAbove)
 
        
        peopleOptions = self.findMatchPeople(matchesLeft,personLeft,matchesAbove, personAbove)
        peopleOptions = [person for person in peopleOptions if person in people]
        if len(peopleOptions)==0: return None
        scores = [self.CompositeScore(person, personLeft, personAbove) for person in peopleOptions]
        minScore = min(scores)
        bestPerson = peopleOptions[scores.index(minScore)]
        return bestPerson
        
    
    
    def newPosition(self,row,col):
        if col==self.numCols-1: 
            col =0
            row += 1
        else: col+=1
        return row,col
    def setLeftToZero(self,row,col):
        row,col = self.newPosition(row,col)
        while row!=self.numRows:
            self.Chart[row][col]=0
            row,col = self.newPosition(row,col)
            
    
    def createString(self, row, col, people):

        if row == self.numRows: return
        newPerson = self.lowestCompositeScore(row, col, people)
        nrow,ncol = self.newPosition(row,col)
        if newPerson==None:
            print(row,col)
            if len(people)==0:
                #self.setLeftToZero(row,col)
                print(self.Chart)
                
                return
            
            elif col==self.numCols-1:
                row,col = self.newPosition(row,col)
                self.createString(nrow, ncol, people)
                
            else: 
                
                #for x in people:
                #min(len(people),2)
                for newPerson in random.sample(people,1):
                    self.Chart[row][col] = newPerson
                    newpeople = self.removePersonFromPeople(newPerson, people)
                    self.createString(nrow, ncol, newpeople)
                

        else:  
        
            self.Chart[row][col] = newPerson
            newpeople = self.removePersonFromPeople(newPerson, people)

            self.createString(nrow, ncol, newpeople)
    
   
    
    
    

In [ ]:
obj = Students()

0 0
2 0
3 0
3 2
4 6
5 0
5 3
5 6
6 3
7 0
7 2
7 8
8 0
8 4
8 5
8 6
8 9
9 0
9 2
9 4
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 17. 16. 49.  9. 28. 51. 78. 74.]
 [83. 59. 72. 93. 91. 20. 70. 89.  8.  0.]
 [ 2. 61. 94. 62. 55.  0.  0.  0.  0.  0.]]
9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 17. 16. 49.  9. 28. 51. 78. 74.]
 [83. 59. 72. 93. 91. 20. 70. 89.  8.  0.]
 [ 2. 61. 55. 94. 62.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]

9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 17. 16. 49.  9. 28. 51. 20. 91.]
 [59. 83. 72. 93. 78. 74. 61.  2.  8. 89.]
 [55. 70. 89. 94. 62.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 17. 16. 49.  9. 28. 51. 20. 91.]
 [59. 83. 72. 93. 78. 74. 61.  2.  8. 89.]
 [55. 70. 89. 62. 94.  0.  0.  0.  0.  0.]]
8 8
9 0
9 1
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54

[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 94. 62. 74. 78.  8. 28. 51. 91.]
 [20. 83. 59. 72. 93. 49.  9. 17. 16. 59.]
 [55.  2. 61. 89. 70.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 94. 62. 74. 78.  8. 28. 51. 91.]
 [20. 83. 59. 72. 93. 49.  9. 17. 16. 59.]
 [55.  2. 61. 70. 89.  0.  0.  0.  0.  0.]]
9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15

8 8
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 94. 62. 20. 83. 59. 72. 93. 91.]
 [16. 17. 78. 74. 89. 70.  2. 61. 51. 28.]
 [49.  9.  8. 55. 70.  0.  0.  0.  0.  0.]]
8 9
9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [24. 63. 94. 62. 20. 83. 59. 72. 93. 91.]
 [16. 17. 78. 74. 89. 70.  2. 61. 55. 28.]
 [49.  9.  8. 28. 51.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80

 [20. 24. 63. 70. 89.  0.  0.  0.  0.  0.]]
9 2
9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [61.  2. 49.  9.  8. 78. 74. 28. 51. 91.]
 [17. 16. 55. 59. 83. 72. 93. 94. 62. 93.]
 [70. 89. 20. 24. 63.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85. 13.  1. 12. 11.]
 [82. 36. 46. 31. 27. 86. 42. 69. 39.  3.]
 [32. 41. 30. 14. 58. 81. 37.  4. 21. 38.]
 [61.  2. 49.  9.  8. 78. 74. 28. 51. 91.]
 [17. 16. 55. 59. 83. 72. 93. 94. 62. 93.]
 [70. 89. 20. 63. 24.  0.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 5

...

 [93. 55. 89. 70. 17. 70.  0.  0.  0.  0.]]
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [28. 51. 38. 91. 63. 24. 11. 12.  8. 78.]
 [37.  4. 21. 94. 62. 14. 58. 81. 20. 74.]
 [72. 59. 83.  9. 49. 16. 17. 31. 27. 86.]
 [93. 70. 89. 55. 17. 70.  0.  0.  0.  0.]]
9 1
9 2
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [28. 51. 38. 91. 63. 24. 11. 12.  8. 78.]
 [37.  4. 21. 94. 62. 14. 58. 81. 20. 74.]
 [72. 59. 83.  9. 49. 16. 17. 86. 27. 31.]
 [93. 55. 89. 70. 17. 70.  0.  0.  0.  0.]]
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 7

9 0
9 2
9 4
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 81. 58. 14.  4. 37. 28. 51. 78. 74.]
 [17. 55. 24. 63. 86. 27. 31. 94. 62. 86.]
 [89. 70. 12. 11.  8. 70.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 81. 58. 14.  4. 37. 28. 51. 78. 74.]
 [17. 55. 24. 63. 86. 27. 31. 94. 62. 86.]
 [89. 70.  8. 12. 11. 70.  0.  0.  0.  0.]]
9 2
9 4
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54

[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 81. 58. 14.  4. 37. 28. 51. 78. 74.]
 [94. 62. 31. 27. 86. 11. 12.  8. 55.  8.]
 [70. 89. 17. 63. 24. 70.  0.  0.  0.  0.]]
9 0
9 2
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 81. 58. 14.  4. 37. 28. 51. 78. 74.]
 [94. 62. 31. 27. 86. 11. 12.  8. 70. 89.]
 [24. 63. 17. 55. 24. 70.  0.  0.  0.  0.]]
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68

8 8
8 9
9 0
9 2
9 4
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 24. 63. 31. 27. 86. 81. 58. 14.  4.]
 [55. 78. 74. 51. 28. 37. 12. 11.  8. 89.]
 [89. 70. 62. 94. 17. 70.  0.  0.  0.  0.]]
9 3
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 24. 63. 31. 27. 86. 81. 58. 14.  4.]
 [55. 78. 74. 51. 28. 37. 12. 11.  8. 89.]
 [89. 70. 17. 62. 94. 70.  0.  0.  0.  0.]]
9 5
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56

 [ 8. 94. 62. 55. 62. 70.  0.  0.  0.  0.]]
9 0
9 3
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 24. 63. 14. 58. 81. 37.  4. 28. 51.]
 [17. 27. 86. 31. 70. 89. 12. 11. 94. 62.]
 [74. 78.  8. 55. 62. 70.  0.  0.  0.  0.]]
9 1
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 73. 50. 48. 45.]
 [ 6. 23. 77. 56. 54. 80. 68. 67. 33. 15.]
 [57. 60.  7. 43.  5. 71. 79. 90. 34. 35.]
 [40. 19. 25. 22. 53. 85.  3. 61.  2. 39.]
 [41. 30. 32. 82. 36. 46. 69. 42.  1. 13.]
 [72. 59. 83. 20. 21. 38. 91.  9. 49. 16.]
 [93. 24. 63. 14. 58. 81. 37.  4. 28. 51.]
 [17. 27. 86. 31. 70. 89. 12. 11. 94. 62.]
 [55. 74. 78.  8. 62. 70.  0.  0.  0.  0.]]
9 4
[[10. 84. 75. 52. 18. 76. 44. 64. 26. 47.]
 [29. 87. 65. 88. 66. 92. 7

In [51]:
obj.VerticleHappiness([5, 6, 8, 10, 46, 60])

Number of People with verticle:


In [47]:
df.loc[11]

First Person     12.0
Second person    69.0
Third person     27.0
Fourth person     NaN
Fifth person      NaN
Name: 11, dtype: float64

In [3]:
random.choice([1,2])

1

In [ ]:
#go through every possible random

In [109]:
matches = []
for person,choices in df.iterrows():
        for rank1,choice in enumerate(choices):
            if person > choice: continue
            if not pd.isnull(choice):
                OtherPersonChoices = list(df.loc[choice])
                if person in OtherPersonChoices:
                    rank2 = OtherPersonChoices.index(person)
                    matches.append({"person1":person,"rank1":rank1+1,"person2":choice, "rank2":rank2+1})
                elif np.isnan(OtherPersonChoices).all():
                    matches.append({"person1":person,"rank1":rank1+1,"person2":choice, "rank2":None})
                
            

In [112]:
    def samePeople(self,pair, p1,p2):
        np1, np2 = pair["person1"],pair["person2"]
        if (np1 == p1 and np2==p2) or (np2 == p1 and np1==p2):
            return True
        return False
    
    
    def removeMatch(self,p1,p2, matches):
        return [pair for pair in matches if not self.samePeople(pair,p1,p2)]
    def verticle(self,row,col):
        verticle = []
        if row!=0:
            verticle.append(self.Chart[row-1][col])
        if row!=10:
            verticle.append(self.Chart[row+1][col])
        return verticle

[[1, 13.0],
 [1, 12.0],
 [3, 61.0],
 [3, 39.0],
 [4, 37.0],
 [4, 21.0],
 [5, 43.0],
 [7, 43.0],
 [7, 42.0],
 [8, 78.0],
 [9, 49.0],
 [10, 84.0],
 [10, 29.0],
 [14, 58.0],
 [15, 34.0],
 [15, 33.0],
 [16, 45.0],
 [18, 52.0],
 [19, 25.0],
 [19, 40.0],
 [20, 83.0],
 [21, 38.0],
 [22, 53.0],
 [22, 57.0],
 [26, 48.0],
 [26, 64.0],
 [27, 86.0],
 [27, 31.0],
 [28, 51.0],
 [29, 87.0],
 [31, 86.0],
 [33, 34.0],
 [36, 82.0],
 [38, 51.0],
 [40, 57.0],
 [42, 69.0],
 [44, 64.0],
 [45, 48.0],
 [50, 73.0],
 [52, 76.0],
 [53, 85.0],
 [54, 56.0],
 [54, 80.0],
 [58, 81.0],
 [59, 83.0],
 [59, 72.0],
 [65, 87.0],
 [65, 84.0],
 [66, 88.0],
 [67, 68.0],
 [68, 79.0],
 [70, 89.0],
 [72, 83.0],
 [75, 84.0],
 [77, 88.0]]

In [97]:
np.isnan([1,2,np.nan]).all()

False

In [82]:
df.loc[13]

First Person      1.0
Second person    78.0
Third person     12.0
Fourth person    34.0
Fifth person     15.0
Name: 13, dtype: float64

In [74]:
matches

[{'person1': 1, 'rank1': 1, 'person2': 13.0, 'rank2': 1},
 {'person1': 1, 'rank1': 2, 'person2': 12.0, 'rank2': 1},
 {'person1': 1, 'rank1': 3, 'person2': 78.0, 'rank2': 2},
 {'person1': 1, 'rank1': 4, 'person2': 8.0, 'rank2': 3},
 {'person1': 1, 'rank1': 5, 'person2': 34.0, 'rank2': 3},
 {'person1': 2, 'rank1': 1, 'person2': 61.0, 'rank2': 3},
 {'person1': 2, 'rank1': 2, 'person2': 42.0, 'rank2': 5},
 {'person1': 2, 'rank1': 3, 'person2': 39.0, 'rank2': 2},
 {'person1': 2, 'rank1': 4, 'person2': 3.0, 'rank2': 3},
 {'person1': 2, 'rank1': 5, 'person2': 69.0, 'rank2': 4},
 {'person1': 3, 'rank1': 1, 'person2': 61.0, 'rank2': 1},
 {'person1': 3, 'rank1': 2, 'person2': 39.0, 'rank2': 1},
 {'person1': 3, 'rank1': 4, 'person2': 69.0, 'rank2': 5},
 {'person1': 4, 'rank1': 1, 'person2': 37.0, 'rank2': 2},
 {'person1': 4, 'rank1': 2, 'person2': 21.0, 'rank2': 2},
 {'person1': 4, 'rank1': 3, 'person2': 14.0, 'rank2': 5},
 {'person1': 4, 'rank1': 4, 'person2': 28.0, 'rank2': 4},
 {'person1': 4, 